In [25]:
# ✨  MONO Modal-Resonator Bank  ✨
# ------------------------------------------------
%pip install --quiet --upgrade numpy soundfile IPython

import numpy as np, soundfile as sf
from math import pi, cos
from IPython.display import Audio, display

# ---------- helpers ------------------------------------------------
def modal_frequencies(f1, n):                 # swap with Bessel roots later
    return [f1 * (m + 1) for m in range(n)]   # 1×,2×,3× … harmonic approx.

def excite(ms=5, fs=48_000):
    n  = int(fs * ms * 1e-3)
    burst = 0.3 * np.random.randn(n)          # -10 dBFS noise
    t  = np.arange(n) / fs
    env = np.exp(-t * 800)                    # 1.25 ms envelope
    return burst * env

# ---------- ModalResonator (no Q, mono) ----------------------------
class ModalResonator:
    def __init__(self, f0, t60, fs):
        self.fs = fs
        self.set_mode(f0, t60)
        self.y1 = self.y2 = 0.0

    def set_mode(self, f0, t60):
        r  = 10 ** (-3 / (t60 * self.fs))
        w0 = 2 * pi * f0 / self.fs
        self.a1 = -2 * r * cos(w0)
        self.a2 =  r * r
        self.g  = 1.0                       # unit impulse → unit peak

    def process(self, x):
        y = self.g * x - self.a1*self.y1 - self.a2*self.y2
        self.y2, self.y1 = self.y1, y
        return y

# ---------- ResonatorBank (mono sum) -------------------------------
class ResonatorBank:
    def __init__(self, f1=140, n=16, t60=3.0, slope=-9, fs=48_000,
                 ring_gain=0.4):
        self.ring_gain = ring_gain
        self.modes = []
        for f in modal_frequencies(f1, n):
            t = t60 * 10**((slope/6)*np.log2(f/f1))   # faster decay for highs
            self.modes.append(ModalResonator(f, t, fs))

    def process(self, x):
        acc = 0.0
        for m in self.modes:
            acc += m.process(x)
        return self.ring_gain * acc                  # scale entire ring

# ---------- render -------------------------------------------------
fs         = 48_000
dry_mix    = 0.03           # stick level
t60_base   = 10.0           # base decay
ring_gain  = 0.1            # overall ring loudness

inp  = np.concatenate([excite(5, fs),
                       np.zeros(fs * int(t60_base * 4))])

bank = ResonatorBank(f1=140, n=16, t60=t60_base,
                     slope=-9, fs=fs, ring_gain=ring_gain)

out  = np.zeros_like(inp)

for n, x in enumerate(inp):
    out[n] = dry_mix * x + bank.process(x)

# ---------- normalise & save --------------------------------------
out = np.nan_to_num(out)
peak = np.max(np.abs(out))
if peak > 0:
    out /= peak                                  # 0 dBFS
sf.write("drum_ping_mono.wav", np.clip(out, -1, 1), fs, subtype="PCM_16")

print(f"Wrote drum_ping_mono.wav  •  {len(out)/fs:.2f} s mono")
display(Audio("drum_ping_mono.wav"))

Note: you may need to restart the kernel to use updated packages.
Wrote drum_ping_mono.wav  •  40.01 s mono
